<a href="https://colab.research.google.com/github/AmarJha/NLP_BERT/blob/master/Use_bert_for_COLA_GLUE_Benchamrk.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
!pip install pytorch-pretrained-bert pytorch-nlp

     |████████████████████████████████| 133kB 7.8MB/s 
     |████████████████████████████████| 92kB 42.6MB/s 
     |████████████████████████████████| 655kB 61.9MB/s 
  Created wheel for regex: filename=regex-2019.8.19-cp36-cp36m-linux_x86_64.whl size=609227 sha256=853b13f0e8d44bac42b9a4d1ccc046998a53463168c0f7880041e77c56e05754
  Stored in directory: /root/.cache/pip/wheels/90/04/07/b5010fb816721eb3d6dd64ed5cc8111ca23f97fdab8619b5be
Successfully built regex


In [0]:
import torch
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from pytorch_pretrained_bert import BertTokenizer, BertConfig
from pytorch_pretrained_bert import BertAdam, BertForSequenceClassification
from tqdm import tqdm, trange
import pandas as pd
import io
import numpy as np
import matplotlib.pyplot as plt
% matplotlib inline

Using TensorFlow backend.


## Model Parameters

In [0]:
from google.colab import files
uploaded = files.upload()

Saving train.tsv to train.tsv


###  Model Class

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
df = pd.read_csv("train.tsv", delimiter='\t', header=None, names=['sentence_source', 'label', 'label_notes', 'sentence'])

## Data representation class

In [0]:
df.shape

(8551, 4)

In [0]:
df.head()

sentence_source  ...                                           sentence
0            gj04  ...  Our friends won't buy this analysis, let alone...
1            gj04  ...  One more pseudo generalization and I'm giving up.
2            gj04  ...   One more pseudo generalization or I'm giving up.
3            gj04  ...     The more we study verbs, the crazier they get.
4            gj04  ...          Day by day the facts are getting murkier.

[5 rows x 4 columns]

In [0]:
sentences = df.sentence.values

# We need to add special tokens at the beginning and end of each sentence for BERT to work properly
sentences = ["[CLS] " + sentence + " [SEP]" for sentence in sentences]
labels = df.label.values

In [0]:
sentences

["[CLS] Our friends won't buy this analysis, let alone the next one we propose. [SEP]",
 "[CLS] One more pseudo generalization and I'm giving up. [SEP]",
 "[CLS] One more pseudo generalization or I'm giving up. [SEP]",
 '[CLS] The more we study verbs, the crazier they get. [SEP]',
 '[CLS] Day by day the facts are getting murkier. [SEP]',
 "[CLS] I'll fix you a drink. [SEP]",
 '[CLS] Fred watered the plants flat. [SEP]',
 '[CLS] Bill coughed his way out of the restaurant. [SEP]',
 "[CLS] We're dancing the night away. [SEP]",
 '[CLS] Herman hammered the metal flat. [SEP]',
 '[CLS] The critics laughed the play off the stage. [SEP]',
 '[CLS] The pond froze solid. [SEP]',
 '[CLS] Bill rolled out of the room. [SEP]',
 '[CLS] The gardener watered the flowers flat. [SEP]',
 '[CLS] The gardener watered the flowers. [SEP]',
 '[CLS] Bill broke the bathtub into pieces. [SEP]',
 '[CLS] Bill broke the bathtub. [SEP]',
 '[CLS] They drank the pub dry. [SEP]',
 '[CLS] They drank the pub. [SEP]',
 '[CLS

In [0]:
df.head()

sentence_source  ...                                           sentence
0            gj04  ...  Our friends won't buy this analysis, let alone...
1            gj04  ...  One more pseudo generalization and I'm giving up.
2            gj04  ...   One more pseudo generalization or I'm giving up.
3            gj04  ...     The more we study verbs, the crazier they get.
4            gj04  ...          Day by day the facts are getting murkier.

[5 rows x 4 columns]

In [0]:
df.tail()

sentence_source  ...                                      sentence
8546            ad03  ...              Poseidon appears to own a dragon
8547            ad03  ...                Digitize is my happiest memory
8548            ad03  ...                It is easy to slay the Gorgon.
8549            ad03  ...  I had the strangest feeling that I knew you.
8550            ad03  ...           What all did you get for Christmas?

[5 rows x 4 columns]

In [0]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', do_lower_case=True)

tokenized_texts = [tokenizer.tokenize(sent) for sent in sentences]
print ("Tokenize the first sentence:")
print (len(tokenized_texts[1]))

100%|██████████| 231508/231508 [00:00<00:00, 904738.32B/s]


Tokenize the first sentence:
14


MAX_LEN = 128

In [0]:
MAX_LEN = 128

## Training warmup 

In [0]:
input_ids = pad_sequences([tokenizer.convert_tokens_to_ids(txt) for txt in tokenized_texts],
                          maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")

In [0]:
input_ids = [tokenizer.convert_tokens_to_ids(x) for x in tokenized_texts]
print(input_ids[1])

[101, 2028, 2062, 18404, 2236, 3989, 1998, 1045, 1005, 1049, 3228, 2039, 1012, 102]


In [0]:
input_ids = pad_sequences(input_ids, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
input_ids[1]

array([  101,  2028,  2062, 18404,  2236,  3989,  1998,  1045,  1005,
        1049,  3228,  2039,  1012,   102,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0]

In [0]:
attention_masks = []
#print(input_ids[1])
# Create a mask of 1s for each token followed by 0s for padding
for seq in input_ids:
  print(seq)
  seq_mask = [int(i>0) for i in seq]
  attention_masks.append(seq_mask)
 

  

[  101  2256  2814  2180  1005  1056  4965  2023  4106  1010  2292  2894
  1996  2279  2028  2057 16599  1012   102     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0]
[  101  2028  2062 18404  2236  3989  1998  1045  1005  1049  3228  2039
  1012   102     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[ 101 2984 2741 1037 2338 2000 3021 1012  102    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0]
[ 101 2984 4604 1037 2338 1012  102    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0

In [0]:
print(attention_masks[0])

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]


In [0]:

train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(input_ids, labels, 
                                                            random_state=2018, test_size=0.1)
train_masks, validation_masks, _, _ = train_test_split(attention_masks, input_ids,
                                             random_state=2018, test_size=0.1)

In [0]:

train_inputs = torch.tensor(train_inputs)
validation_inputs = torch.tensor(validation_inputs)
train_labels = torch.tensor(train_labels)
validation_labels = torch.tensor(validation_labels)
train_masks = torch.tensor(train_masks)
validation_masks = torch.tensor(validation_masks)

In [0]:
batch_size = 32

# Create an iterator of our data with torch DataLoader. This helps save on memory during training because, unlike a for loop, 
# with an iterator the entire dataset does not need to be loaded into memory

train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)


In [0]:
model = BertForSequenceClassification.from_pretrained("bert-base-uncased", num_labels=2)
model.cuda()

In [0]:
param_optimizer = list(model.named_parameters())
no_decay = ['bias', 'gamma', 'beta']
optimizer_grouped_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)],
     'weight_decay_rate': 0.01},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)],
     'weight_decay_rate': 0.0}
]


In [0]:
print(optimizer_grouped_parameters)

In [0]:
optimizer = BertAdam(optimizer_grouped_parameters,
                     lr=2e-5,
                     warmup=.1)

t_total value of -1 results in schedule not being applied


In [0]:
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()
    return np.sum(pred_flat == labels_flat) / len(labels_flat)

In [0]:
# Store our loss and accuracy for plotting
train_loss_set = []
device = 0

# Number of training epochs (authors recommend between 2 and 4)
epochs = 4

# trange is a tqdm wrapper around the normal python range
for _ in trange(epochs, desc="Epoch"):
  
  
  # Training
  
  # Set our model to training mode (as opposed to evaluation mode)
  model.train()
  
  # Tracking variables
  tr_loss = 0
  nb_tr_examples, nb_tr_steps = 0, 0
  
  # Train the data for one epoch
  for step, batch in enumerate(train_dataloader):
    # Add batch to GPU
    batch = tuple(t.to(device) for t in batch)
    # Unpack the inputs from our dataloader
    b_input_ids, b_input_mask, b_labels = batch
    # Clear out the gradients (by default they accumulate)
    optimizer.zero_grad()
    # Forward pass
    loss = model(b_input_ids, token_type_ids=None, attention_mask=b_input_mask, labels=b_labels)
    train_loss_set.append(loss.item())    
    # Backward pass
    loss.backward()
    # Update parameters and take a step using the computed gradient
    optimizer.step()
    
    
    # Update tracking variables
    tr_loss += loss.item()
    nb_tr_examples += b_input_ids.size(0)
    nb_tr_steps += 1

  print("Train loss: {}".format(tr_loss/nb_tr_steps))
    
  device=0
  # Validation

  # Put model in evaluation mode to evaluate loss on the validation set
  model.eval()

  # Tracking variables 
  eval_loss, eval_accuracy = 0, 0
  nb_eval_steps, nb_eval_examples = 0, 0

  # Evaluate data for one epoch
  for batch in validation_dataloader:
    # Add batch to GPU
    batch = tuple(t.to(device) for t in batch)
    # Unpack the inputs from our dataloader
    b_input_ids, b_input_mask, b_labels = batch
    # Telling the model not to compute or store gradients, saving memory and speeding up validation
    with torch.no_grad():
      # Forward pass, calculate logit predictions
      logits = model(b_input_ids, token_type_ids=None, attention_mask=b_input_mask)
    
    # Move logits and labels to CPU
    logits = logits.detach().cpu().numpy()
    label_ids = b_labels.to('cpu').numpy()

    tmp_eval_accuracy = flat_accuracy(logits, label_ids)
    
    eval_accuracy += tmp_eval_accuracy
    nb_eval_steps += 1

  print("Validation Accuracy: {}".format(eval_accuracy/nb_eval_steps))

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Train loss: 0.49197165921515945


Epoch:  25%|██▌       | 1/4 [03:26<10:18, 206.07s/it]

Validation Accuracy: 0.7920524691358025
Train loss: 0.23417714406655044


Epoch:  50%|█████     | 2/4 [06:52<06:52, 206.10s/it]

Validation Accuracy: 0.8260030864197531
Train loss: 0.11584896123600946


Epoch:  75%|███████▌  | 3/4 [10:18<03:26, 206.06s/it]

Validation Accuracy: 0.8283179012345678
Train loss: 0.06591522001131936


Epoch: 100%|██████████| 4/4 [13:44<00:00, 206.04s/it]

Validation Accuracy: 0.8256172839506173


In [0]:
# Store our loss and accuracy for plotting
train_loss_set = []
device = 0

# Number of training epochs (authors recommend between 2 and 4)
epochs = 4

# trange is a tqdm wrapper around the normal python range
for _ in trange(epochs, desc="Epoch"):
  
  
  # Training
  
  # Set our model to training mode (as opposed to evaluation mode)
  model.train()
  
  # Tracking variables
  tr_loss = 0
  nb_tr_examples, nb_tr_steps = 0, 0
  
#   Train the data for one epoch
for step, batch in enumerate(train_dataloader):
#   print(step,batch)
  
    # Add batch to GPU
    batch = tuple(t.to(device) for t in batch)
#     print(batch,"ok")
#     # Unpack the inputs from our dataloader
    b_input_ids, b_input_mask, b_labels = batch
#     # Clear out the gradients (by default they accumulate)
    optimizer.zero_grad()
#     # Forward pass
    loss = model(b_input_ids, token_type_ids=None, attention_mask=b_input_mask, labels=b_labels)
    print(loss,"ok")
#     train_loss_set.append(loss.item())    
#     # Backward pass
#     loss.backward()
#     # Update parameters and take a step using the computed gradient
#     optimizer.step()
    
    
#     # Update tracking variables
#     tr_loss += loss.item()
#     nb_tr_examples += b_input_ids.size(0)
#     nb_tr_steps += 1

#   print("Train loss: {}".format(tr_loss/nb_tr_steps))
    
#   device=0
#   # Validation

#   # Put model in evaluation mode to evaluate loss on the validation set
#   model.eval()

#   # Tracking variables 
#   eval_loss, eval_accuracy = 0, 0
#   nb_eval_steps, nb_eval_examples = 0, 0

#   # Evaluate data for one epoch
#   for batch in validation_dataloader:
#     # Add batch to GPU
#     batch = tuple(t.to(device) for t in batch)
#     # Unpack the inputs from our dataloader
#     b_input_ids, b_input_mask, b_labels = batch
#     # Telling the model not to compute or store gradients, saving memory and speeding up validation
#     with torch.no_grad():
#       # Forward pass, calculate logit predictions
#       logits = model(b_input_ids, token_type_ids=None, attention_mask=b_input_mask)
    
#     # Move logits and labels to CPU
#     logits = logits.detach().cpu().numpy()
#     label_ids = b_labels.to('cpu').numpy()

#     tmp_eval_accuracy = flat_accuracy(logits, label_ids)
    
#     eval_accuracy += tmp_eval_accuracy
#     nb_eval_steps += 1


Epoch: 100%|██████████| 4/4 [00:00<00:00, 813.44it/s]


tensor(0.0436, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0587, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0246, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0098, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0344, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.1428, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0110, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0145, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0288, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0088, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0210, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0842, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0125, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0257, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.0117, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0.1656, device='cuda:0', grad_fn=<NllLossBackward>) ok
tensor(0

In [0]:
# Upload the test file from your local drive
from google.colab import files
uploaded = files.upload()


Saving dev.tsv to dev.tsv


In [0]:
df = pd.read_csv("dev.tsv", delimiter='\t', header=None, names=['sentence_source', 'label', 'label_notes', 'sentence'])

# Create sentence and label lists
sentences = df.sentence.values

# We need to add special tokens at the beginning and end of each sentence for BERT to work properly
sentences = ["[CLS] " + sentence + " [SEP]" for sentence in sentences]
labels = df.label.values

tokenized_texts = [tokenizer.tokenize(sent) for sent in sentences]


MAX_LEN = 128
# Pad our input tokens
input_ids = pad_sequences([tokenizer.convert_tokens_to_ids(txt) for txt in tokenized_texts],
                          maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
# Use the BERT tokenizer to convert the tokens to their index numbers in the BERT vocabulary
input_ids = [tokenizer.convert_tokens_to_ids(x) for x in tokenized_texts]
input_ids = pad_sequences(input_ids, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
# Create attention masks
attention_masks = []

# Create a mask of 1s for each token followed by 0s for padding
for seq in input_ids:
  seq_mask = [float(i>0) for i in seq]
  attention_masks.append(seq_mask) 

prediction_inputs = torch.tensor(input_ids)
prediction_masks = torch.tensor(attention_masks)
prediction_labels = torch.tensor(labels)
  
batch_size = 32  


prediction_data = TensorDataset(prediction_inputs, prediction_masks, prediction_labels)
prediction_sampler = SequentialSampler(prediction_data)
prediction_dataloader = DataLoader(prediction_data, sampler=prediction_sampler, batch_size=batch_size)

In [0]:
model.eval()

# Tracking variables 
predictions , true_labels = [], []

# Predict 
for batch in prediction_dataloader:
  # Add batch to GPU
  batch = tuple(t.to(device) for t in batch)
  # Unpack the inputs from our dataloader
  b_input_ids, b_input_mask, b_labels = batch
  # Telling the model not to compute or store gradients, saving memory and speeding up prediction
  with torch.no_grad():
    # Forward pass, calculate logit predictions
    logits = model(b_input_ids, token_type_ids=None, attention_mask=b_input_mask)

  # Move logits and labels to CPU
  logits = logits.detach().cpu().numpy()
  label_ids = b_labels.to('cpu').numpy()
  
  # Store predictions and true labels
  predictions.append(logits)
  true_labels.append(label_ids)

In [0]:
from sklearn.metrics import matthews_corrcoef
matthews_set = []

for i in range(len(true_labels)):
  matthews = matthews_corrcoef(true_labels[i],
                 np.argmax(predictions[i], axis=1).flatten())
  matthews_set.append(matthews)

In [0]:
matthews_set

[0.3110855084191276,
 0.29814239699997197,
 0.4700159919404217,
 0.4526019054848144,
 0.687932430407656,
 0.5807564950208268,
 0.4133804997216296,
 0.8563488385776753,
 0.5691908489504616,
 0.53748384988657,
 0.647150228929434,
 0.8958064164776167,
 0.42857142857142855,
 0.7867957924694432,
 0.6285648694397382,
 0.6457765999379483,
 -0.07460470969529907,
 -0.1856953381770519,
 -0.3126409456585232,
 0.7453559924999299,
 0.014456362470655182,
 0.5962847939999439,
 0.4472135954999579,
 0.4526019054848144,
 0.632183908045977,
 0.7092993656151906,
 0.7311261550139309,
 0.7125253031944253,
 0.5719694409972929,
 0.8958064164776167,
 0.5465943944999485,
 0.4133804997216296,
 -0.10206207261596575]

In [0]:
flat_predictions = [item for sublist in predictions for item in sublist]
flat_predictions = np.argmax(flat_predictions, axis=1).flatten()
flat_true_labels = [item for sublist in true_labels for item in sublist]


In [0]:
matthews_corrcoef(flat_true_labels, flat_predictions)

0.5155383069979991